In [1]:
import pandas as pd 
from datetime import datetime 
from datetime import date
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from keras.models import Sequential
from keras.layers import LSTM, Dense
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler,StandardScaler
from keras.callbacks import ModelCheckpoint
import tensorflow as tf

In [2]:
merged = pd.read_csv(r'../data/long_merge.csv')

In [7]:
zones = [72, 71, 63, 62, 60, 59, 58,57, 50, 49, 44, 43, 35, 34, 33, 32, 31, 30, 29, 28, ]
rtus = [2]
cols = []

for zone in zones:
        for column in merged.columns:
            if f"zone_0{zone}" in column and 'co2' not in column and "hw_valve" not in column and "cooling_sp" not in column and "heating_sp" not in column:
                cols.append(column)

for zone in zones:
        for column in merged.columns:
              if f"zone_0{zone}" in column: 
                if "cooling_sp" in column or "heating_sp" in column:
                  cols.append(column)
# for rtu in rtus:
#     for column in merged.columns:
#         if f"rtu_00{rtu}_fltrd_sa" in column:
#                 cols.append(column)
cols =['date'] + cols + ['air_temp_set_1',
 'air_temp_set_2',
 'dew_point_temperature_set_1d',
 'relative_humidity_set_1',
 'solar_radiation_set_1']
input_dataset = merged[cols]

In [11]:
input_dataset['date'] = pd.to_datetime(input_dataset['date'], format = "%Y-%m-%d %H:%M:%S")
df_filtered = input_dataset[ (input_dataset.date.dt.date >date(2019, 3, 1)) & (input_dataset.date.dt.date< date(2021, 1, 1))]

if df_filtered.isna().any().any():
    print("There are NA values in the DataFrame columns.")

C:\Users\arbal\AppData\Local\Temp\ipykernel_34660\1855433847.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  input_dataset['date'] = pd.to_datetime(input_dataset['date'], format = "%Y-%m-%d %H:%M:%S")


In [12]:
df_filtered

date  zone_072_temp  zone_072_fan_spd  zone_071_temp  \
511205  2019-03-02 00:00:00           71.2              40.0           71.5   
511206  2019-03-02 00:01:00           71.2              40.0           71.5   
511207  2019-03-02 00:02:00           71.2              40.0           71.5   
511208  2019-03-02 00:03:00           71.2              40.0           71.5   
511209  2019-03-02 00:04:00           71.2              40.0           71.4   
...                     ...            ...               ...            ...   
2072148 2020-12-31 23:57:00           69.5              40.0           71.2   
2072149 2020-12-31 23:58:00           69.5              40.0           71.3   
2072150 2020-12-31 23:58:00           69.5              40.0           71.3   
2072151 2020-12-31 23:59:00           69.5              40.0           71.5   
2072152 2020-12-31 23:59:00           69.5              40.0           71.5   

         zone_071_fan_spd  zone_063_temp  zone_063_fan_spd  zone_062_temp  \
511205               20.0           72.3              20.0           72.9   
511206               20.0           72.3              20.0           72.9   
511207               20.0           72.3              20.0           72.6   
511208               20.0           72.3              20.0           72.9   
511209               20.0           72.3              20.0           72.9   
...                   ...            ...               ...            ...   
2072148              20.0           68.0              20.0           67.6   
2072149              20.0           68.0              20.0           67.6   
2072150              20.0           68.0              20.0           67.6   
2072151              20.0           68.0              20.0           67.6   
2072152              20.0           68.0              20.0           67.6   

         zone_062_fan_spd  zone_059_temp  ...  zone_035_heating_sp  \
511205               55.0           71.9  ...                 70.0   
511206               55.0           71.9  ...                 70.0   
511207               55.0           71.9  ...                 70.0   
511208               55.0           71.9  ...                 70.0   
511209               55.0           71.9  ...                 70.0   
...                   ...            ...  ...                  ...   
2072148              40.0           67.5  ...                 68.0   
2072149              40.0           67.5  ...                 68.0   
2072150              40.0           67.5  ...                 68.0   
2072151              40.0           67.5  ...                 68.0   
2072152              40.0           67.5  ...                 68.0   

         zone_032_cooling_sp  zone_032_heating_sp  zone_030_cooling_sp  \
511205             74.000000                 68.0                 73.0   
511206             74.000000                 68.0                 73.0   
511207             74.000000                 68.0                 73.0   
511208             74.000000                 68.0                 73.0   
511209             74.000000                 68.0                 73.0   
...                      ...                  ...                  ...   
2072148            72.714138                 71.0                 71.0   
2072149            72.714138                 71.0                 71.0   
2072150            72.714138                 71.0                 71.0   
2072151            72.714138                 71.0                 71.0   
2072152            72.714138                 71.0                 71.0   

         zone_030_heating_sp  air_temp_set_1  air_temp_set_2  \
511205                  67.0          11.590          11.130   
511206                  67.0          11.590          11.130   
511207                  67.0          11.590          11.130   
511208                  67.0          11.590          11.130   
511209                  67.0          11.590          11.130   
...                      ...       

In [13]:
testdataset_df = df_filtered[(df_filtered.date.dt.date >date(2020, 3, 1)) & (df_filtered.date.dt.date <date(2020,7, 1))]

# traindataset_df = df_filtered[ (df_filtered.date.dt.date >date(2019, 11, 8))]

traindataset_df = df_filtered[(df_filtered.date.dt.date >date(2019, 3, 1)) & (df_filtered.date.dt.date <date(2020, 3, 1)) | (df_filtered.date.dt.date >date(2020, 7, 1)) & (df_filtered.date.dt.date <date(2020, 12, 1))]
testdataset = testdataset_df.drop(columns=["date"]).values
traindataset = traindataset_df.drop(columns=["date"]).values

columns_with_na = traindataset_df.columns[traindataset_df.isna().any()].tolist()
columns_with_na

[]

In [20]:
traindataset_df.columns[0:31]

Index(['date', 'zone_072_temp', 'zone_072_fan_spd', 'zone_071_temp',
       'zone_071_fan_spd', 'zone_063_temp', 'zone_063_fan_spd',
       'zone_062_temp', 'zone_062_fan_spd', 'zone_059_temp',
       'zone_059_fan_spd', 'zone_058_temp', 'zone_058_fan_spd',
       'zone_057_temp', 'zone_057_fan_spd', 'zone_049_temp',
       'zone_049_fan_spd', 'zone_044_temp', 'zone_044_fan_spd',
       'zone_043_temp', 'zone_043_fan_spd', 'zone_035_temp',
       'zone_035_fan_spd', 'zone_033_temp', 'zone_033_fan_spd',
       'zone_032_temp', 'zone_032_fan_spd', 'zone_030_temp',
       'zone_030_fan_spd', 'zone_028_temp', 'zone_028_fan_spd'],
      dtype='object')

In [14]:
print(traindataset_df.isna().sum().sum(), testdataset_df.isna().sum().sum())

0 0


In [15]:
len(traindataset), len(testdataset)

(1073512, 391818)

In [16]:
traindataset = traindataset.astype('float32')
testdataset = testdataset.astype('float32')

scaler = StandardScaler()
traindataset = scaler.fit_transform(traindataset)
testdataset = scaler.transform(testdataset)

In [17]:
traindataset.shape

(1073512, 55)

In [21]:
train,test = traindataset,testdataset

def create_dataset(dataset,time_step):
    x = []
    Y = []
    for i in range(len(dataset) - time_step - 1):
        x.append(dataset[i:(i+time_step),:])
        Y.append(dataset[i+time_step,0:31])
    x= np.array(x)
    Y = np.array(Y)
    return x,Y
time_step = 30
X_train, y_train = create_dataset(train, time_step)
X_test, y_test = create_dataset(test, time_step)



In [22]:
X_train.shape, y_train.shape

((1073481, 30, 55), (1073481, 31))

In [24]:

model = Sequential()
model.add(LSTM(units=50, return_sequences=True, input_shape=(X_train.shape[1], X_train.shape[2])))
model.add(LSTM(units=50, return_sequences=True))
model.add(LSTM(units=30))
model.add(Dense(units=y_train.shape[1]))

model.compile(optimizer='adam', loss='mean_squared_error')

checkpoint_path = "lstm_vav_02.tf"
checkpoint_callback = ModelCheckpoint(filepath=checkpoint_path, monitor='val_loss', verbose=1, save_best_only=True, mode='min')
model.fit(X_train, y_train, validation_data=(X_test, y_test), epochs=5, batch_size=128, verbose=1, callbacks=[checkpoint_callback])

Epoch 1/5
8386/8387 [============================>.] - ETA: 0s - loss: 0.0512
Epoch 1: val_loss improved from inf to 0.29908, saving model to lstm_vav_02.tf
INFO:tensorflow:Assets written to: lstm_vav_02.tf\assets


INFO:tensorflow:Assets written to: lstm_vav_02.tf\assets


8387/8387 [==============================] - 337s 40ms/step - loss: 0.0512 - val_loss: 0.2991
Epoch 2/5
8387/8387 [==============================] - ETA: 0s - loss: 0.0213
Epoch 2: val_loss improved from 0.29908 to 0.23285, saving model to lstm_vav_02.tf
INFO:tensorflow:Assets written to: lstm_vav_02.tf\assets


INFO:tensorflow:Assets written to: lstm_vav_02.tf\assets


8387/8387 [==============================] - 300s 36ms/step - loss: 0.0213 - val_loss: 0.2328
Epoch 3/5
8387/8387 [==============================] - ETA: 0s - loss: 0.0152
Epoch 3: val_loss did not improve from 0.23285
8387/8387 [==============================] - 359s 43ms/step - loss: 0.0152 - val_loss: 0.2426
Epoch 4/5
8387/8387 [==============================] - ETA: 0s - loss: 0.0106
Epoch 4: val_loss did not improve from 0.23285
8387/8387 [==============================] - 350s 42ms/step - loss: 0.0106 - val_loss: 0.2556
Epoch 5/5
8386/8387 [============================>.] - ETA: 0s - loss: 0.0096
Epoch 5: val_loss did not improve from 0.23285
8387/8387 [==============================] - 349s 42ms/step - loss: 0.0096 - val_loss: 0.2635


In [14]:
model.load_weights(checkpoint_path)

In [25]:
test_predict1 = model.predict(X_test)

12244/12244 [==============================] - 60s 5ms/step


In [35]:
%matplotlib qt
plt.figure()
var = 1
plt.plot(y_test[:,var], label='Original Testing Data', color='blue')
plt.plot(test_predict1[:,var], label='Predicted Testing Data', color='red',alpha=0.8)
anomalies = np.where(abs(test_predict1[:,var] - y_test[:,var]) > 0.38)
plt.scatter(anomalies,test_predict1[anomalies,var], color='black',marker ="o",s=100 )


plt.title('Testing Data - Predicted vs Actual')
plt.xlabel('Time')
plt.ylabel('Value')
plt.legend()
plt.show()

In [36]:
%matplotlib qt
test_predict2 = model.predict(X_train)



33547/33547 [==============================] - 201s 6ms/step


ValueError: operands could not be broadcast together with shapes (1073481,) (391787,) 

In [39]:
plt.figure()
var = 3
plt.plot(y_train[:,var], label='Original Training Data', color='blue')
plt.plot(test_predict2[:,var], label='Predicted Training Data', color='red',alpha=0.8)
anomalies = np.where(abs(test_predict2[:,var] - y_train[:,var]) > 0.38)
plt.scatter(anomalies,test_predict2[anomalies,var], color='black',marker ="o",s=100 )


plt.title('Training Data - Predicted vs Actual')
plt.xlabel('Time')
plt.ylabel('Value')
plt.legend()
plt.show()

In [29]:
from sklearn.mixture import GaussianMixture
import numpy as np
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA


# Generating random data for demonstration
np.random.seed(0)
X =  test_predict1 - y_test


pca = PCA(n_components=2)
X = pca.fit_transform(X)


# Creating the GMM instance with desired number of clusters
gmm = GaussianMixture(n_components=2)

# Fitting the model to the data
gmm.fit(X)

# Getting the cluster labels
labels = gmm.predict(X)

# Plotting the data points with colors representing different clusters
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.title('GMM Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [30]:
from sklearn.cluster import KMeans
import numpy as np
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA

# Generating random data for demonstration
np.random.seed(0)
X = (test_predict1 - y_test)

k = 6

kmeans = KMeans(n_clusters=k)

kmeans.fit(X)


pca = PCA(n_components=2)
X = pca.fit_transform(X)



# Getting the cluster centers and labels
centroids = kmeans.cluster_centers_
centroids = pca.transform(centroids)
labels = kmeans.labels_

# Plotting the data points and cluster centers
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.scatter(centroids[:, 0], centroids[:, 1], marker='x', c='red', s=200, linewidths=2)
plt.title('KMeans Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [32]:
k = 60
X= test_predict1 - y_test
processed_data = []
feat_df = pd.DataFrame(columns=["mean","std",])
for i in range(0,len(X), 60):
    mean = X[i:i+k].mean(axis = 0)
    std = X[i:i+k].std(axis = 0)
    max = X[i:i+k].max(axis = 0)
    min = X[i:i+k].min(axis = 0)
    iqr = np.percentile(X[i:i+k], 75, axis=0) - np.percentile(X[i:i+k], 25,axis=0)
    data = np.concatenate([mean, std, max, min, iqr])
    processed_data.append([data])
processed_data = np.concatenate(processed_data,axis=0) 

In [34]:
X = processed_data

kmeans = KMeans(n_clusters=2, algorithm='elkan', max_iter=1000, n_init = 5)

kmeans.fit(X)

pca = PCA(n_components=2)
X = pca.fit_transform(X)


# Getting the cluster centers and labels
centroids = kmeans.cluster_centers_
centroids = pca.transform(centroids)
labels = kmeans.labels_

# Plotting the data points and cluster centers
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.scatter(centroids[:, 0], centroids[:, 1], marker='x', c='red', s=200, linewidths=2)
plt.title('KMeans Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [21]:
from sklearn.mixture import GaussianMixture
import numpy as np
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA

# Generating random data for demonstration
np.random.seed(0)
X = processed_data

# Creating the GMM instance with desired number of clusters
gmm = GaussianMixture(n_components=2, init_params='k-means++')

# Fitting the model to the data
gmm.fit(X)
labels = gmm.predict(X)


pca = PCA(n_components=2)
X = pca.fit_transform(X)


# Getting the cluster labels

# Plotting the data points with colors representing different clusters
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.title('GMM Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()



In [38]:
from sklearn.cluster import KMeans
import numpy as np
import matplotlib.pyplot as plt
# Generating random data for demonstration
np.random.seed(0)
X = test_predict1 - y_test 

kmeans = KMeans(n_clusters=2)

kmeans.fit(X)


pca = PCA(n_components=2)
X = pca.fit_transform(X)



# Getting the cluster centers and labels
centroids = kmeans.cluster_centers_
centroids = pca.transform(centroids)
labels = kmeans.labels_

# Plotting the data points and cluster centers
plt.figure()
plt.scatter(X[:, 0], X[:, 1], c=labels, cmap='viridis', alpha=0.5)
plt.scatter(centroids[:, 0], centroids[:, 1], marker='x', c='red', s=200, linewidths=2)
plt.text(centroids[0,0], centroids[0,1], 'Normal', fontsize=12, color='red')
plt.text(centroids[1,0], centroids[1,1], 'Anomaly', fontsize=12, color='red')
plt.title('KMeans Clustering')
plt.xlabel('Feature 1')
plt.ylabel('Feature 2')
plt.show()


In [29]:
sum(labels==0)

329810